In [29]:
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

import pandas as pd

from IPython.display import HTML
import cartopy.crs as ccrs
ds = xr.open_zarr('gs://weatherbench2/datasets/hres_t0/2016-2022-6h-1440x721.zarr')

In [ ]:
class WeatherData:
    def __init__(self, ds: xr.Dataset) -> None:
        self.ds = ds
    
    def select_data(self, variables: list, horizon: int = 36, offset: int = 0, year = 2020) -> None:
        

        self.latitude = np.arange(-35 - offset, -22.75 + offset, 0.25) 
        self.longitude = np.arange(16 - offset, 33.25 + offset, 0.25) 

        self.level = 850 # hPa

        # Print selection criteria
        print(f"Latitude: {self.latitude.min()} to {self.latitude.max()}")
        print(f"Longitude: {self.longitude.min()} to {self.longitude.max()}")
        print(f"Level: {self.level} hPa")
        
        self.ds = self.ds[variables]
        if year > 0:
            self.year = year
            self.ds = self.ds.sel(time=slice(f'{self.year}-01-01', f'{self.year}-12-31'))
            print(f"Year: {year}")

        self.ds = self.ds.sel(level=self.level)
        self.ds = self.ds.sel(latitude=slice(self.latitude.min(), self.latitude.max()), longitude=slice(self.longitude.min(), self.longitude.max()))
        if horizon > 0:
            self.horizon = int(horizon * 1e9 * 3600 + 1)
            print(f"Horizon: {horizon} days")
            self.ds = self.ds.sel(prediction_timedelta=slice(np.timedelta64(0, 'ns'), np.timedelta64(self.horizon, 'ns')))

    def load_data(self) -> None:
        self.ds.load()

    def describe_data(self) -> None:
        print(self.ds.coords)

    def plot_from_forecasts(self, seed: int = 0, frame_rate: int = 8, levels: int = 10, 
                     variables: list = ['geopotential', 'wind_speed', 'temperature', 'specific_humidity']) -> HTML:

        sample = self.ds[variables]

        sample = sample.isel(time=seed)

        seed_time = sample.time.values

        timedeltas = pd.to_timedelta(sample.prediction_timedelta.values, unit='ns')

        times_at_seed_plus_delta = pd.to_datetime(seed_time) + timedeltas

        formatted_times = times_at_seed_plus_delta.strftime('%Y-%m-%dT%H:%M:%S.') + times_at_seed_plus_delta.nanosecond.astype(str).str.zfill(9)

        bounds = [sample.longitude.min().item(), sample.longitude.max().item(),
                sample.latitude.min().item(), sample.latitude.max().item()]
        
        print(bounds)

        latitudes = sample.latitude.values
        longitudes = sample.longitude.values

        lon_grid, lat_grid = np.meshgrid(latitudes, longitudes)

        n_columns = 2
        n_rows = int(np.ceil(len(variables) / n_columns))

        # Set up the figure and axes with dynamic rows and 2 columns
        fig, axs = plt.subplots(n_rows, n_columns, figsize=(14, 7 * n_rows), 
                                subplot_kw={'projection': ccrs.PlateCarree()})
        
        fig.subplots_adjust(left=0.05, right=0.95, bottom=0.1, top=0.9, wspace=0.2, hspace=0.2)

        # Flatten the axes array for easy indexing
        axs = axs.flatten()

        for i, variable in enumerate(variables):
            print(f"Variable: {variable}")

            ax = axs[i]
            
            ax.coastlines()
            ax.set_extent(bounds, crs=ccrs.PlateCarree())
            vmin = sample[variable].values.min()
            vmax = sample[variable].values.max()
            feat = ax.contourf(lat_grid, lon_grid, sample[variable].values[0], levels=levels, vmin=vmin, vmax=vmax, transform=ccrs.PlateCarree())
            fig.colorbar(feat, ax=ax, orientation="vertical", label=f"{variable} levels", shrink=0.7, pad=0.02)

            ax.set_title(f"{variable} - {formatted_times[0]}")


        def animate(i):
            print(f"Frame: {i}/{len(sample.prediction_timedelta)}", end='\r')
            for j, variable in enumerate(variables):
                ax = axs[j]
                ax.clear() 
                
                ax.coastlines()
                ax.set_extent(bounds, crs=ccrs.PlateCarree())
                
                vmin = sample[variable].values.min()
                vmax = sample[variable].values.max()
                
                feat = ax.contourf(lat_grid, lon_grid, sample[variable].values[i], levels=levels, vmin=vmin, vmax=vmax,  transform=ccrs.PlateCarree())
                ax.set_title(f"{variable} - {formatted_times[i]}")
            return feat,

        frames = len(sample.prediction_timedelta)

        interval = 1000 / frame_rate

        ani = FuncAnimation(fig, animate, frames=frames, interval=interval)

        plt.close(fig)

        return HTML(ani.to_jshtml())
    
    def plot_ground_truth(self, seed: int = 0, steps: int = 7, frame_rate: int = 8, levels: int = 10, 
                     variables: list = ['geopotential', 'wind_speed', 'temperature', 'specific_humidity']) -> HTML:

        sample = self.ds[variables]

        sample = sample.isel(time=slice(seed, seed + steps))

        seed_time = sample.time.values
        print(seed_time)

        bounds = [sample.longitude.min().item(), sample.longitude.max().item(),
                sample.latitude.min().item(), sample.latitude.max().item()]
        
        print(bounds)

        latitudes = sample.latitude.values
        longitudes = sample.longitude.values

        transposed = False
        lon_grid, lat_grid = np.meshgrid(latitudes, longitudes)

        if lon_grid.shape != sample[variables[0]].values[0].shape:
            print("Transposing grid")
            lon_grid, lat_grid = np.meshgrid(longitudes, latitudes)
            transposed = True

        n_columns = 2
        n_rows = int(np.ceil(len(variables) / n_columns))

        fig, axs = plt.subplots(n_rows, n_columns, figsize=(14, 7 * n_rows), 
                                subplot_kw={'projection': ccrs.PlateCarree()})
        
        fig.subplots_adjust(left=0.05, right=0.95, bottom=0.1, top=0.9, wspace=0.2, hspace=0.2)

        axs = axs.flatten()

        for i, variable in enumerate(variables):
            print(f"Variable: {variable}")

            ax = axs[i]
            
            ax.coastlines()
            ax.set_extent(bounds, crs=ccrs.PlateCarree())
            vmin = sample[variable].values.min()
            vmax = sample[variable].values.max()

            plot_sample = sample[variable].values[0]

            if transposed:
                feat = ax.contourf(lon_grid, lat_grid, plot_sample, levels=levels, vmin=vmin, vmax=vmax, transform=ccrs.PlateCarree())
            else:   
                feat = ax.contourf(lat_grid, lon_grid, plot_sample, levels=levels, vmin=vmin, vmax=vmax, transform=ccrs.PlateCarree())

            fig.colorbar(feat, ax=ax, orientation="vertical", label=f"{variable} levels", shrink=0.7, pad=0.02)

            ax.set_title(f"{variable} - {seed_time[0]}")


        def animate(i):
            
            for j, variable in enumerate(variables):
                print(f"Frame: {i}/{steps} - Variable: {variable}", end='\r')
                ax = axs[j]
                ax.clear() 
                
                ax.coastlines()
                ax.set_extent(bounds, crs=ccrs.PlateCarree())
                
                vmin = sample[variable].values.min()
                vmax = sample[variable].values.max()
                plot_sample = sample[variable].values[i]

                if transposed:
                    feat = ax.contourf(lon_grid, lat_grid, plot_sample, levels=levels, vmin=vmin, vmax=vmax, transform=ccrs.PlateCarree())
                else:   
                    feat = ax.contourf(lat_grid, lon_grid, plot_sample, levels=levels, vmin=vmin, vmax=vmax, transform=ccrs.PlateCarree())

                ax.set_title(f"{variable} - {seed_time[i]}")
            return feat,

        frames = steps

        interval = 1000 / frame_rate

        ani = FuncAnimation(fig, animate, frames=frames, interval=interval)

        plt.close(fig)

        return HTML(ani.to_jshtml())



In [88]:
weather_data = WeatherData(ds)

In [89]:
weather_data.ds

<xarray.Dataset> Size: 4TB
Dimensions:                  (time: 10268, latitude: 721, longitude: 1440,
                              level: 13)
Coordinates:
  * latitude                 (latitude) float32 3kB -90.0 -89.75 ... 89.75 90.0
  * level                    (level) int32 52B 50 100 150 200 ... 850 925 1000
  * longitude                (longitude) float32 6kB 0.0 0.25 ... 359.5 359.8
  * time                     (time) datetime64[ns] 82kB 2016-01-01 ... 2023-0...
Data variables: (12/14)
    10m_u_component_of_wind  (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    10m_v_component_of_wind  (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    10m_wind_speed           (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    2m_temperature           (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    geopotential             (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>
    mean_sea_level_pressure  (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    ...                       ...
    temperature              (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>
    total_precipitation_6hr  (time, latitude, longitude) float32 43GB dask.array<chunksize=(1, 721, 1440), meta=np.ndarray>
    u_component_of_wind      (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>
    v_component_of_wind      (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>
    vertical_velocity        (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>
    wind_speed               (time, level, latitude, longitude) float32 554GB dask.array<chunksize=(1, 13, 721, 1440), meta=np.ndarray>

In [90]:
variables = ['geopotential', 'wind_speed', 'temperature', 'specific_humidity', 'vertical_velocity', 'v_component_of_wind', 'u_component_of_wind']
weather_data.select_data(variables=variables, horizon=0, offset=5)

Latitude: -40.0 to -18.0
Longitude: 11.0 to 38.0
Level: 850 hPa


In [91]:
weather_data.describe_data()

Coordinates:
  * latitude   (latitude) float32 356B -40.0 -39.75 -39.5 ... -18.5 -18.25 -18.0
    level      int32 4B 850
  * longitude  (longitude) float32 436B 11.0 11.25 11.5 ... 37.5 37.75 38.0
  * time       (time) datetime64[ns] 82kB 2016-01-01 ... 2023-01-10T18:00:00


In [92]:
weather_data.ds

<xarray.Dataset> Size: 3GB
Dimensions:              (time: 10268, latitude: 89, longitude: 109)
Coordinates:
  * latitude             (latitude) float32 356B -40.0 -39.75 ... -18.25 -18.0
    level                int32 4B 850
  * longitude            (longitude) float32 436B 11.0 11.25 11.5 ... 37.75 38.0
  * time                 (time) datetime64[ns] 82kB 2016-01-01 ... 2023-01-10...
Data variables:
    geopotential         (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    wind_speed           (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    temperature          (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    specific_humidity    (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    vertical_velocity    (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    v_component_of_wind  (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>
    u_component_of_wind  (time, latitude, longitude) float32 398MB dask.array<chunksize=(1, 89, 109), meta=np.ndarray>

In [94]:
weather_data.plot_ground_truth(seed=0, steps=24, frame_rate=8, levels=10, variables=['geopotential', 'wind_speed', 'temperature', 'specific_humidity'])



['2016-01-01T00:00:00.000000000' '2016-01-01T06:00:00.000000000'
 '2016-01-01T12:00:00.000000000' '2016-01-01T18:00:00.000000000'
 '2016-01-02T00:00:00.000000000' '2016-01-02T06:00:00.000000000'
 '2016-01-02T12:00:00.000000000' '2016-01-02T18:00:00.000000000'
 '2016-01-03T00:00:00.000000000' '2016-01-03T06:00:00.000000000'
 '2016-01-03T12:00:00.000000000' '2016-01-03T18:00:00.000000000'
 '2016-01-04T00:00:00.000000000' '2016-01-04T06:00:00.000000000'
 '2016-01-04T12:00:00.000000000' '2016-01-04T18:00:00.000000000'
 '2016-01-05T00:00:00.000000000' '2016-01-05T06:00:00.000000000'
 '2016-01-05T12:00:00.000000000' '2016-01-05T18:00:00.000000000'
 '2016-01-06T00:00:00.000000000' '2016-01-06T06:00:00.000000000'
 '2016-01-06T12:00:00.000000000' '2016-01-06T18:00:00.000000000']
[11.0, 38.0, -40.0, -18.0]
Transposing grid
Variable: geopotential
Variable: wind_speed
Variable: temperature
Variable: specific_humidity
